# Pipeline Run Example

Simple run of the the pipeline to serve as guide

In [1]:
from src.pipeline.BasePipeline import BasePipeline
from src.dataloader import PartialCSVDataLoader
from src.retriever import BM25
from src.llms import Gemma2, Llama3_1
# from src.vector_store import ChromaVectorStore
from langchain.embeddings import HuggingFaceBgeEmbeddings


/home/caio.rhoden/miniconda3/envs/datamodels/lib/python3.11/site-packages/pydantic/_internal/_fields.py:161: UserWarning: Field "model_name" has conflict with protected namespace "model_".

You may be able to resolve this warning by setting `model_config['protected_namespaces'] = ()`.
  warnings.warn(
/home/caio.rhoden/miniconda3/envs/datamodels/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="2"

In [3]:
train_dataloader = PartialCSVDataLoader('../data/instruction-induction-data/raw/induce_tasks_examples.csv')

In [4]:
# train_dataloader.get_documents()[:5]

In [5]:
# test_dataloader.get_documents()[:5]

In [6]:
embedding_model = HuggingFaceBgeEmbeddings(model_name="dunzhang/stella_en_400M_v5", model_kwargs={"device": "cuda:0", "trust_remote_code":True}, encode_kwargs = {"normalize_embeddings": True})

Some weights of the model checkpoint at dunzhang/stella_en_400M_v5 were not used when initializing NewModel: ['new.pooler.dense.bias', 'new.pooler.dense.weight']
- This IS expected if you are initializing NewModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing NewModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


RuntimeError: CUDA error: out of memory
CUDA kernel errors might be asynchronously reported at some other API call, so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1
Compile with `TORCH_USE_CUDA_DSA` to enable device-side assertions.


In [7]:
pipe = BasePipeline(
    retriever=BM25(),
    dataloader=train_dataloader,
    llm=Llama3_1(),
    device="cuda:0",
)

`low_cpu_mem_usage` was None, now set to True since model is quantized.
Loading checkpoint shards: 100%|██████████| 4/4 [02:35<00:00, 38.75s/it]


In [8]:
result = pipe.run("The actor sued the professor", 5)
print(result)

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


vectorizer=<rank_bm25.BM25Okapi object at 0x7fc720a20290> docs=[Document(page_content='The tourist supported the authors.\nThe authors were supported by the tourist.'), Document(page_content='The athlete contacted the tourists.\nThe tourists were contacted by the athlete.'), Document(page_content='The judges believed the bankers.\nThe bankers were believed by the judges.'), Document(page_content='The president encouraged the actor.\nThe actor was encouraged by the president.'), Document(page_content='The lawyers believed the authors.\nThe authors were believed by the lawyers.'), Document(page_content='The senator advised the doctors.\nThe doctors were advised by the senator.'), Document(page_content='The authors advised the student.\nThe student was advised by the authors.'), Document(page_content='The secretaries believed the tourists.\nThe tourists were believed by the secretaries.'), Document(page_content='The tourists recommended the bankers.\nThe bankers were recommended by the to

/home/caio.rhoden/miniconda3/envs/datamodels/lib/python3.11/site-packages/bitsandbytes/nn/modules.py:435: UserWarning: Input type into Linear4bit is torch.float16, but bnb_4bit_compute_dtype=torch.float32 (default). This will lead to slow inference or training speed.
  warnings.warn(



            Fill the expected Output
        
            Examples:
            The actor supported the professor.
The professor was supported by the actor. 

The actor stopped the professor.
The professor was stopped by the actor. 

The actor admired the professor.
The professor was admired by the actor. 

The actor thanked the professor.
The professor was thanked by the actor. 

The actor recommended the professor.
The professor was recommended by the actor. 


            Input:
            The actor sued the professor

            Output:
         The professor was sued by the actor. 

         """
            # Define the verb conjugations
            verb_conjugations = {
               'stopped': 'was stopped by',
                'admirer': 'was admired by',
                'thanks': 'was thanked by',
               'recommended': 'was recommended by',
               'sued': 'was sued by',
               'supported': 'was supported by',
               'stopped': 'was stopped by

In [9]:
result

'\n            Fill the expected Output\n        \n            Examples:\n            The actor supported the professor.\nThe professor was supported by the actor. \n\nThe actor stopped the professor.\nThe professor was stopped by the actor. \n\nThe actor admired the professor.\nThe professor was admired by the actor. \n\nThe actor thanked the professor.\nThe professor was thanked by the actor. \n\nThe actor recommended the professor.\nThe professor was recommended by the actor. \n\n\n            Input:\n            The actor sued the professor\n\n            Output:\n         The professor was sued by the actor. \n\n         """\n            # Define the verb conjugations\n            verb_conjugations = {\n               \'stopped\': \'was stopped by\',\n                \'admirer\': \'was admired by\',\n                \'thanks\': \'was thanked by\',\n               \'recommended\': \'was recommended by\',\n               \'sued\': \'was sued by\',\n               \'supported\': \'wa

## Run Tests Example

In [10]:
import pandas as pd
test = pd.read_csv('../data/instruction-induction-data/raw/execute_tasks_examples.csv').loc[:200]
test.head()

task                                   input  \
0  active_to_passive     The professor mentioned the artist.   
1  active_to_passive  The presidents recommended the lawyer.   
2  active_to_passive    The professors thanked the tourists.   
3  active_to_passive      The scientist contacted the judge.   
4  active_to_passive        The doctor stopped the managers.   

                                          output  
0     The artist was mentioned by the professor.  
1  The lawyer was recommended by the presidents.  
2   The tourists were thanked by the professors.  
3      The judge was contacted by the scientist.  
4       The managers were stopped by the doctor.

In [11]:
# pipe.run_tests(
#     test_data = test,
#     checkpoint = 0,
#     checkpoints_step= 50,
#     k = 8,
#     run_tag = "example_test_run"
# )